In [14]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [15]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [16]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [17]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [18]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [19]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [24]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[7:8]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)[34:]
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2017-2019
--//--Scrapping data for scheme:  RAMAI AWAAS YOJNA FOR SC
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--//--Scrapping data for district:  AHMEDNAGAR
--//--//--//--//--Scrapping data for block:  AKOLA
--//--//--//--//--Scrapping data for block:  JAMKHED
--//--//--//--//--Scrapping data for block:  KARJAT
--//--//--//--//--Scrapping data for block:  KOPARGAON
--//--//--//--

--//--//--//--//--Scrapping data for block:  JALGAON
--//--//--//--//--Scrapping data for block:  JAMNER
--//--//--//--//--Scrapping data for block:  MUKTAINAGAR
--//--//--//--//--Scrapping data for block:  PACHORA
--//--//--//--//--Scrapping data for block:  PAROLA
--//--//--//--//--Scrapping data for block:  RAVER
--//--//--//--//--Scrapping data for block:  YAWAL
--//--//--//--Scrapping data for district:  JALNA
--//--//--//--//--Scrapping data for block:  AMBAD
--//--//--//--//--Scrapping data for block:  BADNAPUR
--//--//--//--//--Scrapping data for block:  BHOKARDAN
--//--//--//--//--Scrapping data for block:  GHANSAVANGI
--//--//--//--//--Scrapping data for block:  JAFRABAD
--//--//--//--//--Scrapping data for block:  JALNA
--//--//--//--//--Scrapping data for block:  MANTHA
--//--//--//--//--Scrapping data for block:  PARTUR
--//--//--//--Scrapping data for district:  KOLHAPUR
--//--//--//--//--Scrapping data for block:  AJRA
--//--//--//--//--Scrapping data for block:  BAVDA
-

--//--//--//--//--Scrapping data for block:  GUHAGAR
--//--//--//--//--Scrapping data for block:  KHED
--//--//--//--//--Scrapping data for block:  LANJA
--//--//--//--//--Scrapping data for block:  MANDANGAD
--//--//--//--//--Scrapping data for block:  RAJAPUR
--//--//--//--//--Scrapping data for block:  RATNAGIRI
--//--//--//--//--Scrapping data for block:  SANGAMESHWAR
--//--//--//--Scrapping data for district:  SANGLI
--//--//--//--//--Scrapping data for block:  ATPADI
--//--//--//--//--Scrapping data for block:  JATH
--//--//--//--//--Scrapping data for block:  KADEGAON
--//--//--//--//--Scrapping data for block:  KAVATHE-MAHANKAL
--//--//--//--//--Scrapping data for block:  KHANAPUR
--//--//--//--//--Scrapping data for block:  MIRAJ
--//--//--//--//--Scrapping data for block:  PALUS
--//--//--//--//--Scrapping data for block:  SHIRALA
--//--//--//--//--Scrapping data for block:  TASGAON
--//--//--//--//--Scrapping data for block:  WALWA
--//--//--//--Scrapping data for district: 

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--//--Scrapping data for district:  AHMEDNAGAR
--//--//--//--//--Scrapping data for block:  AKOLA
--//--//--//--//--Scrapping data for block:  JAMKHED
--//--//--//--//--Scrapping data for block:  KARJAT
--//--//--//--//--Scrapping data for block:  KOPARGAON
--//--//--//--//--Scrapping data for block:  NAGAR
--//--//--//--//--Scrapping data for block:  NEVASA
--//--//

--//--//--//--//--Scrapping data for block:  JAMNER
--//--//--//--//--Scrapping data for block:  MUKTAINAGAR
--//--//--//--//--Scrapping data for block:  PACHORA
--//--//--//--//--Scrapping data for block:  PAROLA
--//--//--//--//--Scrapping data for block:  RAVER
--//--//--//--//--Scrapping data for block:  YAWAL
--//--//--//--Scrapping data for district:  JALNA
--//--//--//--//--Scrapping data for block:  AMBAD
--//--//--//--//--Scrapping data for block:  BADNAPUR
--//--//--//--//--Scrapping data for block:  BHOKARDAN
--//--//--//--//--Scrapping data for block:  GHANSAVANGI
--//--//--//--//--Scrapping data for block:  JAFRABAD
--//--//--//--//--Scrapping data for block:  JALNA
--//--//--//--//--Scrapping data for block:  MANTHA
--//--//--//--//--Scrapping data for block:  PARTUR
--//--//--//--Scrapping data for district:  KOLHAPUR
--//--//--//--//--Scrapping data for block:  AJRA
--//--//--//--//--Scrapping data for block:  BAVDA
--//--//--//--//--Scrapping data for block:  BHUDARGAD

--//--//--//--//--Scrapping data for block:  LANJA
--//--//--//--//--Scrapping data for block:  MANDANGAD
--//--//--//--//--Scrapping data for block:  RAJAPUR
--//--//--//--//--Scrapping data for block:  RATNAGIRI
--//--//--//--//--Scrapping data for block:  SANGAMESHWAR
--//--//--//--Scrapping data for district:  SANGLI
--//--//--//--//--Scrapping data for block:  ATPADI
--//--//--//--//--Scrapping data for block:  JATH
--//--//--//--//--Scrapping data for block:  KADEGAON
--//--//--//--//--Scrapping data for block:  KAVATHE-MAHANKAL
--//--//--//--//--Scrapping data for block:  KHANAPUR
--//--//--//--//--Scrapping data for block:  MIRAJ
--//--//--//--//--Scrapping data for block:  PALUS
--//--//--//--//--Scrapping data for block:  SHIRALA
--//--//--//--//--Scrapping data for block:  TASGAON
--//--//--//--//--Scrapping data for block:  WALWA
--//--//--//--Scrapping data for district:  SATARA
--//--//--//--//--Scrapping data for block:  JAOLI
--//--//--//--//--Scrapping data for block: 

--//--//--//--//--Scrapping data for block:  BHANPURA
--//--//--//--//--Scrapping data for block:  GAROTH
--//--//--//--//--Scrapping data for block:  MALHARGARH
--//--//--//--//--Scrapping data for block:  MANDSAUR
--//--//--//--//--Scrapping data for block:  SITAMAU
--//--//--//--Scrapping data for district:  MORENA
--//--//--//--Scrapping data for district:  NARSINGHPUR
--//--//--//--Scrapping data for district:  NEEMUCH
--//--//--//--Scrapping data for district:  PANNA
--//--//--//--Scrapping data for district:  RAISEN
--//--//--//--Scrapping data for district:  RAJGARH
--//--//--//--Scrapping data for district:  RATLAM
--//--//--//--Scrapping data for district:  REWA
--//--//--//--Scrapping data for district:  SAGAR
--//--//--//--Scrapping data for district:  SATNA
--//--//--//--Scrapping data for district:  SEHORE
--//--//--//--Scrapping data for district:  SEONI
--//--//--//--Scrapping data for district:  SHAHDOL
--//--//--//--Scrapping data for district:  SHAJAPUR
--//--//--//-

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--//--Scrapping data for district:  ANGUL
--//--//--//--Scrapping data for district:  BALESHWAR
--//--//--//--//--Scrapping data for block:  B

In [18]:
df = pd.concat(df_list)

In [19]:
df

#SNo              Panchayat Name  Houses completed for prior to 2012-2013  \
1    1.0                      Barama                                        0   
2    2.0                   Debachara                                        0   
3    3.0                   Kaklabari                                        0   
4    4.0                   Kharuajan                                        0   
5    5.0                    Merkuchi                                        0   
6    6.0                 Puransripur                                        0   
1    1.0                    Adalbari                                        0   
2    2.0                      Ambari                                        0   
3    3.0                   Athiabari                                        0   
4    4.0                 Banganabari                                        0   
5    5.0                  Bathouguri                                        0   
6    6.0                    Bhogpara                                        0   
7    7.0                     Borbari                                        0   
8    8.0                      Doomni                                        0   
9    9.0                    Madhupur                                        0   
10  10.0                  Narayanpur                                        0   
11  11.0                     Nikashi                                        0   
12  12.0                      Thamna                                        0   
1    1.0                        Adla                                        0   
2    2.0                  Angardhowa                                        0   
3    3.0                   Baganpara                                        0   
4    4.0                  Bagulamari                                        0   
5    5.0                       Gerua                                        0   
6    6.0                   Ghoramara                                        0   
7    7.0                    Jopadong                                        0   
8    8.0                   Pakhamara                                        0   
9    9.0                  Subankhata                                        0   
1    1.0                     Bahbari                                        0   
2    2.0                    Barapeta                                        0   
3    3.0                     Bonmaja                                        0   
..   ...                         ...                                      ...   
30  30.0                        KOSA                                        0   
31  31.0                  KUNDIKHOLA                                        0   
32  32.0                       LAATA                                        0   
33  33.0                   LAM BAGAR                                        0   
34  34.0                      LANGSI                                        0   
35  35.0               LAYYRI-THAINA                                        0   
36  36.0                LYARI THAINA                                        0   
37  37.0                   MAHARGAON                                        0   
38  38.0                      MALARI                                        0   
39  39.0                        MANA                                        0   
40  40.0                      MERUAG                                        0   
41  41.0                       MOLTA                                        0   
42  42.0                       NEETI                                        0   
43  43.0                       PAGNO                                        0   
44  44.0                       PAKHI                                        0   
45  45.0                PANDUKESHWAR                                        0   
46  46.0                        PANI                                        0   
47  47.0                      POKHN

In [22]:
#merge all dataframes to master dataframe
df = pd.concat(df_list)
df = df.reset_index().drop(columns=['index', '#SNo'])
df['#SNo'] = df.index + 1
#Save Scrapped File
df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)